In [31]:
## import libraries
%matplotlib inline
import matplotlib.pyplot as plt 
import gzip, os, sys
import numpy as np
from scipy.stats import multivariate_normal
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import normalize
import warnings

#### Function: load data

In [32]:
## new download to get data from my repo
def download(filename):
    url = 'https://github.com/0tv0renakniga/dsc_255_hw3_minst_data/raw/main'
    file_url = f'{url}/{filename}'
    cmd = f'wget -O {filename} {file_url}'
    os.system(cmd)

# Invokes download() if necessary, then reads in images
def load_mnist_images(filename):
    if not os.path.exists(filename):
        download(filename)
    with gzip.open(filename, 'rb') as f:
        data = np.frombuffer(f.read(), np.uint8, offset=16)
    data = data.reshape(-1,784)
    return data

def load_mnist_labels(filename):
    if not os.path.exists(filename):
        download(filename)
    with gzip.open(filename, 'rb') as f:
        data = np.frombuffer(f.read(), np.uint8, offset=8)
    return data


In [33]:
## load the MNIST training set
train_data = load_mnist_images('train-images-idx3-ubyte.gz')
## normalize the data to be between 0 and 1
train_data = train_data//255
train_labels = load_mnist_labels('train-labels-idx1-ubyte.gz')

## load the MNIST testing set
test_data = load_mnist_images('t10k-images-idx3-ubyte.gz')
## normalize the data to be between 0 and 1
test_data = test_data//255
test_labels = load_mnist_labels('t10k-labels-idx1-ubyte.gz')

#### Function: display digit data 

In [34]:
def displaychar(image):
    plt.imshow(np.reshape(image, (28,28)), cmap=plt.cm.gray)
    plt.axis('off')
    plt.show()

#### Check: The training set consists of 60,000 images. Thus `train_data` should be a 60000x784 array while `train_labels` should be 60000x1. Let's check.

In [35]:
print("Training set size: ", train_data.shape)
print("Training labels size: ", train_labels.shape)

Training set size:  (60000, 784)
Training labels size:  (60000,)


**<font color="magenta">For you to do:</font>** Define a function, **fit_generative_model**, that takes as input a training set (data `x` and labels `y`) and fits a Gaussian generative model to it. It should return the parameters of this generative model; for each label `j = 0,1,...,9`, we have:
* `pi[j]`: the frequency of that label
* `mu[j]`: the 784-dimensional mean vector
* `sigma[j]`: the 784x784 covariance matrix

This means that `pi` is 10x1, `mu` is 10x784, and `sigma` is 10x784x784.

We have already seen how to fit a Gaussian generative model in the Winery example, but now there is an added ingredient. <font color="magenta">The empirical covariances are very likely to be singular (or close to singular), which means that we won't be able to do calculations with them</font>. Thus it is important to **regularize** these matrices. The standard way of doing this is to add `cI` to them, where `c` is some constant and `I` is the 784-dimensional identity matrix. (To put it another way, we compute the empirical covariances and then increase their diagonal entries by some constant `c`.)

This modification is guaranteed to yield covariance matrices that are non-singular, for any `c > 0`, no matter how small. But this doesn't mean that we should make `c` as small as possible. Indeed, `c` is now a parameter, and by setting it appropriately, we can improve the performance of the model. We will study **regularization** in greater detail over the coming weeks.

Your routine needs to choose a good setting of `c`. Crucially, this needs to be done using the training set alone. So you might try setting aside part of the training set as a validation set, or using some kind of cross-validation.

In [41]:
def fit_generative_model(x, y):
    """
    Fit a Gaussian generative model to the data with optimized performance.
    
    Parameters:
    -----------
    x : numpy.ndarray
        Training data of shape (n_samples, n_features)
    y : numpy.ndarray
        Training labels of shape (n_samples,)
        
    Returns:
    --------
    mu : numpy.ndarray
        Mean vectors for each class, shape (k, d)
    sigma : numpy.ndarray
        Covariance matrices for each class, shape (k, d, d)
    pi : numpy.ndarray
        Prior probabilities for each class, shape (k,)
    """
    k = 10  # labels 0,1,...,k-1
    d = x.shape[1]  # number of features (784 for MNIST)
    n = x.shape[0]  # number of samples
    
    # initialize parameters
    mu = np.zeros((k, d))
    sigma = np.zeros((k, d, d))
    pi = np.zeros(k)

    #### you code here
    """
    ------------------------------------------------------------
    STEP 1: calc pi, mu sigma
    ------------------------------------------------------------
    loop over all unique labels 0,1,...,9(i.e n to k-1)
    calc indexes where label is equal to the unique label
    calc pi(class prob) for every unique label
    calc mu(mean vector) for every unique label
    calc sigma(covariance) for every unique labels
        *transform since we want to row to rep features
        *note: this is empirical covariance
    * note: this code return correct dimensions
    ------------------------------------------------------------
    """
    for j in range(k):
        index =  (y==j).flatten()
        pi[j] = np.mean(j==y)
        mu[j] = np.mean(x[index], axis=0)
        sigma[j] = np.cov(x[index].T)

    """
    ------------------------------------------------------------
    STEP 2: find best c for training data
    ------------------------------------------------------------
    initialize values for c to test(c_values)
    Maybe:: split training data(x,y) 80/20 
        * do this since we don't want to overtrain and optimize 
        our c for just the training data
    evaluate performance of each c_val in c_values
    select c_val where errors are minimized

    thought process:
    fit to this such that our prediction given a sample is a 
    specific label moreover, we call this:
                \delta_k(x)=argmax_k p(x|k)p(k)
    or where \delta_k(x) is the maximum will return the predicted class label

    define \delta_k(x) as*:***
    \delta_k(x) = x^T *\Sigma_k^{-1}*\mu_k - 0.5*(\mu_k^T)*\Sigma_k^{-1}*\mu_k + \log(\pi_k))
    -pi_k is the prior probability of class k(i.e. label frequency)
    -x is the sample
    -\mu_k is the mean vector for class k(i.e. what does the average sample look like for each label)
    -sigma_k is the covariance matrix for class k(i.e. how do the samples vary around the mean)
    -w^T is the transform of a vector w
    -np.log is the natural log

    *pg.151 {book name} eq'n: 4.24
    *** ne cu zabusaviti.. trebamo nejki dugaciji equation!!!
    ------------------------------------------------------------
    """


    ## initialize c values to test
    c_values = [0.0001,0.001,0.01,0.1,1,10,100,1000,10000]
    
    ## find best c
    best_c = find_best_regularization(k,d,x,y,c_values)

    ## regularize sigma
    for j in range(k):
        sigma[j] = sigma[j] + best_c*np.eye(d)

    return(mu,sigma,pi)

def find_best_regularization(k,d,x,y,c_values):
    ## initialize train/test(80/20) to evaluate best c 
    X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=33)

    ## initialize best c
    best_c = None
    best_accuracy = 0

    ## initialize mu,sigma,pi, and I to iterate over c_values
    mu = np.zeros((k,d))
    sigma = np.zeros((k,d,d))
    pi = np.zeros(k)
    I = np.eye(d)

    ## initialize y_pred
    y_pred = np.zeros(X_test.shape[0])

    ## loop over c_values
    for c_val in c_values:
        print(f'Testing c value: {c_val}')
        ## calc sigma,mu,pi
        ## note sigma is regularized covariance matrix now
        for j in range(k):
            index =  (y_train==j).flatten()
            pi[j] = np.mean(j==y_train)
            mu[j] = np.mean(X_train[index], axis=0)
            sigma[j] = np.cov(X_train[index].T)+ c_val*I
        
        ## calc prediction
        print(f'Calculating predictions for c value: {c_val}')
    with warnings.catch_warnings():
        warnings.filterwarnings('error', category=RuntimeWarning)
        
        for i in range(X_test.shape[0]):
            max_val = -np.inf
            for j in range(k):
                    # classify each prediction using \delta_k(x) expression
                    # probably defined in that classic book
                try:
                    delta_k = (2*np.pi)**(-d/2) * np.linalg.det(sigma[j])**(-0.5) * np.exp(-0.5*(X_test[i]-mu[j]).dot(np.linalg.inv(sigma[j])).dot(X_test[i]-mu[j]))
                    #delta_k = np.dot(X_test[i], np.linalg.inv(sigma[j])).dot(mu[j]) - 0.5*(mu[j].T).dot(np.linalg.inv(sigma[j])).dot(mu[j]) + np.log(pi[j])
                except RuntimeWarning as e:
                    print(f"RuntimeWarning: {e} for c value: {c_val}")
                    continue
                if delta_k > max_val:
                    max_val = delta_k
                    y_pred[i] = j


        ## calc accuracy
        accuracy = accuracy_score(y_test, y_pred)
        if accuracy > best_accuracy:
            best_accuracy = accuracy
            best_c = c_val

    print(f"Best c value: {best_c} with accuracy: {best_accuracy}")
    return(best_c)


<>:51: SyntaxWarning: invalid escape sequence '\d'
<>:51: SyntaxWarning: invalid escape sequence '\d'
/tmp/ipykernel_399463/2623888821.py:51: SyntaxWarning: invalid escape sequence '\d'
  """


#### Test: Okay, let's try out your function. In particular, we will use **displaychar** to visualize the means of the Gaussians for the first three digits. You can try the other digits on your own.

In [42]:
## calc mu,sigma,pi using fit_generative_model
mu, sigma, pi = fit_generative_model(train_data, train_labels)

## display mu(data average for labels 0,1,2) for each label
displaychar(mu[0])
displaychar(mu[1])
displaychar(mu[2])

Testing c value: 0.0001
Calculating predictions for c value: 0.0001
Testing c value: 0.001
Calculating predictions for c value: 0.001
Testing c value: 0.01
Calculating predictions for c value: 0.01
Testing c value: 0.1
Calculating predictions for c value: 0.1
Testing c value: 1
Calculating predictions for c value: 1
Testing c value: 10
Calculating predictions for c value: 10
Testing c value: 100
Calculating predictions for c value: 100
Testing c value: 1000
Calculating predictions for c value: 1000
Testing c value: 10000
Calculating predictions for c value: 10000


/tmp/ipykernel_399463/2623888821.py:51: SyntaxWarning: invalid escape sequence '\d'
  """


KeyboardInterrupt: 

#### Test: Make predictions on test data

In [ ]:
k=10
# Compute log Pr(label|image) for each [test image,label] pair.
score = np.zeros((len(test_labels),k))
for label in range(0,k):
    rv = multivariate_normal(mean=mu[label], cov=sigma[label])
    for i in range(0,len(test_labels)):
       score[i,label] = np.log(pi[label]) + rv.logpdf(test_data[i,:])
predictions = np.argmax(score, axis=1)
# Finally, tally up score
errors = np.sum(predictions != test_labels)
print("Your model makes " + str(errors) + " errors out of 10000")

#### Quick exercises

<font color="magenta">Exercise 1:</font> What happens if you do not regularize the covariance matrices?

<font color="magenta">Exercise 2:</font> What happens if you set the value of `c` too high, for instance to one billion? Do you understand why this happens?
- plot c(x-axis) vs error(y-axis)

<font color="magenta">Exercise 3:</font> What value of c did you end up using? How many errors did your model make on the training set?
- from other section

<font color="magenta">If you have the time</font>: We have talked about using the same regularization constant `c` for all ten classes. What about using a different value of `c` for each class? How would you go about choosing these? Can you get better performance in this way?